In [38]:
# Most of this code is from Patrick Triest
# See his website here: https://blog.patricktriest.com/
# Modifications to his code are mostly changes to the coins used and visuals

In [1]:
import os
import numpy as np
import pandas as pd
import pickle
import quandl
from datetime import datetime
import plotly.offline as py
import plotly.graph_objs as go
import plotly.figure_factory as ff
py.init_notebook_mode(connected=True)

In [2]:
def get_quandl_data(quandl_id):
    '''Download and cache Quandl dataseries'''
    cache_path = '{}.pkl'.format(quandl_id).replace('/','-')
    try:
        f = open(cache_path, 'rb')
        df = pickle.load(f)   
        print('Loaded {} from cache'.format(quandl_id))
    except (OSError, IOError) as e:
        print('Downloading {} from Quandl'.format(quandl_id))
        df = quandl.get(quandl_id, returns="pandas")
        df.to_pickle(cache_path)
        print('Cached {} at {}'.format(quandl_id, cache_path))
    return df

In [3]:
# Pull Kraken BTC price exchange data
btc_usd_price_kraken = get_quandl_data('BCHARTS/KRAKENUSD')

Cached BCHARTS/KRAKENUSD at BCHARTS-KRAKENUSD.pkl


In [4]:
btc_usd_price_kraken.head()

Open       High        Low      Close  Volume (BTC)  \
Date                                                                   
2014-01-07  874.67040  892.06753  810.00000  810.00000     15.622378   
2014-01-08  810.00000  899.84281  788.00000  824.98287     19.182756   
2014-01-09  825.56345  870.00000  807.42084  841.86934      8.158335   
2014-01-10  839.99000  857.34056  817.00000  857.33056      8.024510   
2014-01-11  858.20000  918.05471  857.16554  899.84105     18.748285   

            Volume (Currency)  Weighted Price  
Date                                           
2014-01-07       13151.472844      841.835522  
2014-01-08       16097.329584      839.156269  
2014-01-09        6784.249982      831.572913  
2014-01-10        6780.220188      844.938794  
2014-01-11       16698.566929      890.671709

In [5]:
# Chart the BTC pricing data
btc_trace = go.Scatter(x=btc_usd_price_kraken.index, y=btc_usd_price_kraken['Weighted Price'])
py.iplot([btc_trace])

In [6]:
# Pull pricing data for 3 more BTC exchanges
exchanges = ['COINBASE','BITSTAMP','ITBIT']

exchange_data = {}

exchange_data['KRAKEN'] = btc_usd_price_kraken

for exchange in exchanges:
    exchange_code = 'BCHARTS/{}USD'.format(exchange)
    btc_exchange_df = get_quandl_data(exchange_code)
    exchange_data[exchange] = btc_exchange_df

Cached BCHARTS/COINBASEUSD at BCHARTS-COINBASEUSD.pkl
Cached BCHARTS/BITSTAMPUSD at BCHARTS-BITSTAMPUSD.pkl
Cached BCHARTS/ITBITUSD at BCHARTS-ITBITUSD.pkl


In [7]:
def merge_dfs_on_column(dataframes, labels, col):
    '''Merge a single column of each dataframe into a new combined dataframe'''
    series_dict = {}
    for index in range(len(dataframes)):
        series_dict[labels[index]] = dataframes[index][col]
        
    return pd.DataFrame(series_dict)

In [8]:
# Merge the BTC price dataseries' into a single dataframe
btc_usd_datasets = merge_dfs_on_column(list(exchange_data.values()), list(exchange_data.keys()), 'Weighted Price')

In [9]:
btc_usd_datasets.tail()

BITSTAMP     COINBASE        ITBIT       KRAKEN
Date                                                          
2017-09-30  4278.295232  4277.663731  4262.221049  4290.117514
2017-10-01  4280.997098  4319.813188  4317.864094  4314.305295
2017-10-02  4394.013069  4402.536107  4396.562923  4409.721658
2017-10-03  4295.104231  4312.974604  4305.215903  4311.757087
2017-10-04  4234.087194  4246.035433  4257.124409  4251.207641

In [10]:
def df_scatter(df, title, seperate_y_axis=False, y_axis_label='', scale='linear', initial_hide=False):
    '''Generate a scatter plot of the entire dataframe'''
    label_arr = list(df)
    series_arr = list(map(lambda col: df[col], label_arr))
    
    layout = go.Layout(
        title=title,
        legend=dict(orientation="h"),
        xaxis=dict(type='date'),
        yaxis=dict(
            title=y_axis_label,
            showticklabels= not seperate_y_axis,
            type=scale
        )
    )
    
    y_axis_config = dict(
        overlaying='y',
        showticklabels=False,
        type=scale )
    
    visibility = 'visible'
    if initial_hide:
        visibility = 'legendonly'
        
    # Form Trace For Each Series
    trace_arr = []
    for index, series in enumerate(series_arr):
        trace = go.Scatter(
            x=series.index, 
            y=series, 
            name=label_arr[index],
            visible=visibility
        )
        
        # Add seperate axis for the series
        if seperate_y_axis:
            trace['yaxis'] = 'y{}'.format(index + 1)
            layout['yaxis{}'.format(index + 1)] = y_axis_config    
        trace_arr.append(trace)

    fig = go.Figure(data=trace_arr, layout=layout)
    py.iplot(fig)

In [11]:
# Plot all of the BTC exchange prices
df_scatter(btc_usd_datasets, 'Bitcoin Price (USD) By Exchange')

In [12]:
# Remove "0" values
btc_usd_datasets.replace(0, np.nan, inplace=True)

In [13]:
# Plot the revised dataframe
df_scatter(btc_usd_datasets, 'Bitcoin Price (USD) By Exchange')

In [14]:
# Calculate the average BTC price as a new column
btc_usd_datasets['avg_btc_price_usd'] = btc_usd_datasets.mean(axis=1)

In [15]:
# Plot the average BTC price
btc_trace = go.Scatter(x=btc_usd_datasets.index, y=btc_usd_datasets['avg_btc_price_usd'])
py.iplot([btc_trace])

In [16]:
def get_json_data(json_url, cache_path):
    '''Download and cache JSON data, return as a dataframe.'''
    try:        
        f = open(cache_path, 'rb')
        df = pickle.load(f)   
        print('Loaded {} from cache'.format(json_url))
    except (OSError, IOError) as e:
        print('Downloading {}'.format(json_url))
        df = pd.read_json(json_url)
        df.to_pickle(cache_path)
        print('Cached {} at {}'.format(json_url, cache_path))
    return df

In [17]:
base_polo_url = 'https://poloniex.com/public?command=returnChartData&currencyPair={}&start={}&end={}&period={}'
start_date = datetime.strptime('2015-01-01', '%Y-%m-%d') # get data from the start of 2015
end_date = datetime.now() # up until today
pediod = 86400 # pull daily data (86,400 seconds per day)

def get_crypto_data(poloniex_pair):
    '''Retrieve cryptocurrency data from poloniex'''
    json_url = base_polo_url.format(poloniex_pair, start_date.timestamp(), end_date.timestamp(), pediod)
    data_df = get_json_data(json_url, poloniex_pair)
    data_df = data_df.set_index('date')
    return data_df

In [48]:
altcoins = ['ETH','LTC','BCH','XMR','SC','GAME','GAS','OMG', 'LSK']

altcoin_data = {}
for altcoin in altcoins:
    coinpair = 'BTC_{}'.format(altcoin)
    crypto_price_df = get_crypto_data(coinpair)
    altcoin_data[altcoin] = crypto_price_df

Loaded https://poloniex.com/public?command=returnChartData&currencyPair=BTC_ETH&start=1420088400.0&end=1507224872.379541&period=86400 from cache
Loaded https://poloniex.com/public?command=returnChartData&currencyPair=BTC_LTC&start=1420088400.0&end=1507224872.379541&period=86400 from cache
Loaded https://poloniex.com/public?command=returnChartData&currencyPair=BTC_BCH&start=1420088400.0&end=1507224872.379541&period=86400 from cache
Loaded https://poloniex.com/public?command=returnChartData&currencyPair=BTC_XMR&start=1420088400.0&end=1507224872.379541&period=86400 from cache
Loaded https://poloniex.com/public?command=returnChartData&currencyPair=BTC_SC&start=1420088400.0&end=1507224872.379541&period=86400 from cache
Loaded https://poloniex.com/public?command=returnChartData&currencyPair=BTC_GAME&start=1420088400.0&end=1507224872.379541&period=86400 from cache
Loaded https://poloniex.com/public?command=returnChartData&currencyPair=BTC_GAS&start=1420088400.0&end=1507224872.379541&period=86

In [49]:
altcoin_data['ETH'].tail()

close      high       low      open   quoteVolume       volume  \
date                                                                            
2017-10-01  0.068979  0.070064  0.068979  0.069563  31119.793516  2162.276722   
2017-10-02  0.067501  0.069136  0.067001  0.068979  43219.384933  2929.611078   
2017-10-03  0.067668  0.068778  0.067000  0.067677  42951.475942  2914.461400   
2017-10-04  0.069210  0.070893  0.067601  0.067727  45706.149648  3158.919320   
2017-10-05  0.068449  0.069779  0.067600  0.069210  36203.116348  2487.604942   

            weightedAverage  
date                         
2017-10-01         0.069482  
2017-10-02         0.067785  
2017-10-03         0.067855  
2017-10-04         0.069114  
2017-10-05         0.068712

In [50]:
altcoin_data['OMG'].tail()

close      high       low      open    quoteVolume      volume  \
date                                                                            
2017-10-01  0.002222  0.002337  0.002183  0.002337   66886.494970  152.552747   
2017-10-02  0.002092  0.002252  0.002050  0.002222  232497.035740  501.036014   
2017-10-03  0.002140  0.002180  0.001971  0.002092  125366.453033  256.419403   
2017-10-04  0.002042  0.002154  0.002030  0.002151   58931.218962  122.404250   
2017-10-05  0.002021  0.002092  0.001975  0.002050   35562.001114   71.984463   

            weightedAverage  
date                         
2017-10-01         0.002281  
2017-10-02         0.002155  
2017-10-03         0.002045  
2017-10-04         0.002077  
2017-10-05         0.002024

In [51]:
# Calculate USD Price as a new column in each altcoin dataframe
for altcoin in altcoin_data.keys():
    altcoin_data[altcoin]['price_usd'] =  altcoin_data[altcoin]['weightedAverage'] * btc_usd_datasets['avg_btc_price_usd']

In [52]:
# Merge USD price of each altcoin into single dataframe 
combined_df = merge_dfs_on_column(list(altcoin_data.values()), list(altcoin_data.keys()), 'price_usd')

In [53]:
# Add BTC price to the dataframe
combined_df['BTC'] = btc_usd_datasets['avg_btc_price_usd']

In [54]:
# Chart all of the altcoin prices
df_scatter(combined_df, 'Cryptocurrency Prices (USD) (Linear)', seperate_y_axis=False, y_axis_label='Coin Value (USD)', scale='linear')

In [55]:
# Chart all of the altcoin prices
df_scatter(combined_df, 'Cryptocurrency Prices (USD) (Log)', seperate_y_axis=False, y_axis_label='Coin Value (USD)', scale='log')

In [56]:
# Calculate the pearson correlation coefficients for cryptocurrencies in 2016
combined_df_2016 = combined_df[combined_df.index.year == 2016]
combined_df_2016.pct_change().corr(method='pearson')

BCH       ETH      GAME  GAS       LSK       LTC  OMG        SC  \
BCH   NaN       NaN       NaN  NaN       NaN       NaN  NaN       NaN   
ETH   NaN  1.000000  0.025612  NaN  0.299749 -0.064652  NaN  0.169642   
GAME  NaN  0.025612  1.000000  NaN -0.055420  0.080741  NaN  0.119564   
GAS   NaN       NaN       NaN  NaN       NaN       NaN  NaN       NaN   
LSK   NaN  0.299749 -0.055420  NaN  1.000000  0.035420  NaN  0.158236   
LTC   NaN -0.064652  0.080741  NaN  0.035420  1.000000  NaN  0.012253   
OMG   NaN       NaN       NaN  NaN       NaN       NaN  NaN       NaN   
SC    NaN  0.169642  0.119564  NaN  0.158236  0.012253  NaN  1.000000   
XMR   NaN  0.087216  0.005709  NaN  0.023479  0.129475  NaN  0.047910   
BTC   NaN -0.006502  0.123653  NaN  0.052344  0.750174  NaN  0.035116   

           XMR       BTC  
BCH        NaN       NaN  
ETH   0.087216 -0.006502  
GAME  0.005709  0.123653  
GAS        NaN       NaN  
LSK   0.023479  0.052344  
LTC   0.129475  0.750174  
OMG        NaN       NaN  
SC    0.047910  0.035116  
XMR   1.000000  0.127520  
BTC   0.127520  1.000000

In [57]:
# Calculate the pearson correlation coefficients for cryptocurrencies in 2017
combined_df_2017 = combined_df[combined_df.index.year == 2017]
combined_df_2017.pct_change().corr(method='pearson')

BCH       ETH      GAME       GAS       LSK       LTC       OMG  \
BCH   1.000000  0.268877  0.154956  0.087834  0.160349  0.394896  0.771894   
ETH   0.268877  1.000000  0.363408  0.111282  0.494197  0.342730  0.863471   
GAME  0.154956  0.363408  1.000000  0.202108  0.352498  0.278497  0.739037   
GAS   0.087834  0.111282  0.202108  1.000000  0.252829  0.303354  0.315023   
LSK   0.160349  0.494197  0.352498  0.252829  1.000000  0.345935  0.821805   
LTC   0.394896  0.342730  0.278497  0.303354  0.345935  1.000000  0.916252   
OMG   0.771894  0.863471  0.739037  0.315023  0.821805  0.916252  1.000000   
SC    0.077183  0.360055  0.579023  0.037111  0.404410  0.344209  0.722638   
XMR   0.093928  0.555291  0.384019  0.237455  0.446603  0.416576  0.837414   
BTC   0.288702  0.476911  0.443966  0.182440  0.440288  0.427531  0.902930   

            SC       XMR       BTC  
BCH   0.077183  0.093928  0.288702  
ETH   0.360055  0.555291  0.476911  
GAME  0.579023  0.384019  0.443966  
GAS   0.037111  0.237455  0.182440  
LSK   0.404410  0.446603  0.440288  
LTC   0.344209  0.416576  0.427531  
OMG   0.722638  0.837414  0.902930  
SC    1.000000  0.330356  0.413150  
XMR   0.330356  1.000000  0.438607  
BTC   0.413150  0.438607  1.000000

In [58]:
def correlation_heatmap(df, title, absolute_bounds=True):
    '''Plot a correlation heatmap for the entire dataframe'''
    heatmap = go.Heatmap(
        z=df.corr(method='pearson').as_matrix(),
        x=df.columns,
        y=df.columns,
        colorbar=dict(title='Pearson Coefficient'),
    )
    
    layout = go.Layout(title=title)
    
    if absolute_bounds:
        heatmap['zmax'] = 1.0
        heatmap['zmin'] = -1.0
        
    fig = go.Figure(data=[heatmap], layout=layout)
    py.iplot(fig)

In [65]:
correlation_heatmap(combined_df_2016.pct_change(), "Correlation of Various Cryptocurrencies in 2016")

In [60]:
correlation_heatmap(combined_df_2017.pct_change(), "Correlation of Various Cryptocurrencies in 2017")

In [66]:
# A red cell means the daily returns of the two intersection cryptocurrencies are very correlated, while a blue cell means there is little correlation.

# While many coins are missing in the 2016 data (because they had yet to be invented yet), for the ones that do exist, they have a much weaker correlation to each other than in 2017.

# Patrick believes the reason why the coins seem to be so correlated now is because hedge funds have started trading cryptocurrencies, and are likely spreading their investments over many coins.